In [1]:
import pandas as pd
import turicreate
import pymysql
import time

conn = pymysql.connect(host='35.201.241.101',  
                       user='staging_cdi', 
                       passwd='w4raAVvIJFGD6xz5k6wQ8nhEV', 
                       db='ccc', 
                       port=3306)
cur = conn.cursor()

df = pd.read_csv('/users/john.tung/Downloads/April_vod.csv')
df.head()

datetime        date      time  day  weekday         accountID  \
0  2020-04-01 19:40:08  2020-04-01  19:40:08    1        3  2A006D97750B308B   
1  2020-04-01 19:31:14  2020-04-01  19:31:14    1        3  2A00B65D5D5B5823   
2  2020-04-01 18:57:36  2020-04-01  18:57:36    1        3  2A00FB754B6E0F0A   
3  2020-04-01 18:38:25  2020-04-01  18:38:25    1        3  2A0056B34E84A185   
4  2020-04-01 18:44:34  2020-04-01  18:44:34    1        3  2A00F9C9ADBEEACF   

  device_type media_type                    assetID  
0          tv        vod  vod10549-000000M001_1500K  
1      mobile        vod  vod40932-000029M001_1500K  
2          tv        vod  vod41211-000078M001_1500K  
3          tv        vod  vod39623-000001M001_1500K  
4      mobile        vod  vod40831-000003M001_1500K

In [2]:
df = df.drop(columns=['datetime', 'date', 'time', 'day', 'weekday', 'device_type', 'media_type'])
df['assetID'] = [id_.split('-')[0] for id_ in df['assetID']]
df.head()

accountID   assetID
0  2A006D97750B308B  vod10549
1  2A00B65D5D5B5823  vod40932
2  2A00FB754B6E0F0A  vod41211
3  2A0056B34E84A185  vod39623
4  2A00F9C9ADBEEACF  vod40831

In [3]:
df = pd.DataFrame({'sum':df.groupby(['accountID', 'assetID']).size()}).reset_index()
df.head()

accountID   assetID  sum
0  2A0000005180228A  vod41382    2
1  2A000000BDFC3956  vod13908   11
2  2A000000BDFC3956  vod19087    6
3  2A000000CB49B1FF  vod42003    1
4  2A0000015AC75284  vod41728    9

In [4]:
data = turicreate.SFrame(df)
data.head()

Columns:
	accountID	str
	assetID	str
	sum	int

Rows: 10

Data:
+------------------+----------+-----+
|    accountID     | assetID  | sum |
+------------------+----------+-----+
| 2A0000005180228A | vod41382 |  2  |
| 2A000000BDFC3956 | vod13908 |  11 |
| 2A000000BDFC3956 | vod19087 |  6  |
| 2A000000CB49B1FF | vod42003 |  1  |
| 2A0000015AC75284 | vod41728 |  9  |
| 2A0000015AC75284 | vod41940 |  2  |
| 2A0000015AC75284 | vod42046 |  4  |
| 2A00000510F26CC4 | vod17762 |  10 |
| 2A00000510F26CC4 | vod41413 |  1  |
| 2A0000051E2EEFEB | vod37760 |  2  |
+------------------+----------+-----+
[10 rows x 3 columns]

In [5]:
ranking_factorization_model = turicreate.ranking_factorization_recommender.create(data, user_id='accountID', item_id='assetID', target='sum')
ranking_factorization_model

Preparing data set.

Data has 351665 observations with 79807 users and 5419 items.

Data prepared in: 0.49137s

Training ranking_factorization_recommender for recommendations.

+--------------------------------+--------------------------------------------------+----------+

...

Optimization Complete: Maximum number of passes through the data reached.

Computing final objective value and training RMSE.

Final objective value: 90.6198

Final training RMSE: 4.28498

Class                            : RankingFactorizationRecommender

Schema
------
User ID                          : accountID
Item ID                          : assetID
Target                           : sum
Additional observation features  : 0
User side features               : []
Item side features               : []

Statistics
----------
Number of observations           : 351665
Number of users                  : 79807
Number of items                  : 5419

Training summary
----------------
Training time                    : 12.5513

Model Parameters
----------------
Model class                      : RankingFactorizationRecommender
num_factors                      : 32
binary_target                    : 0
side_data_factorization          : 1
solver                           : auto
nmf                              : 0
max_iterations                   : 25

Regularization Settings
-----------------------
regularization                   : 0.0
regularization_type              : no

In [6]:
user_list = list(set(df['accountID']))
print(len(user_list), user_list)

79807 ['2A005E25597F901F', '2A00FC2A5756B0E3', '2A002933A89E2195', '2A00FC3EAB6D29E5', '2A00ED27DFAA301C', '2A000A3066472B32', '2A00BB6460EE8382', '2A0022BC39C185DA', '2A00685913E603BE', '2A0002D3077C1B1A', '2A001BE9E78F1EE3', '2A0080E161FBEC03', '2A007AB60D581C88', '2A00E11066A020B7', '2A0051805EB6C0FC', '2A00EF708C3BA02F', '2A001670DBA6FBF9', '2A0037FB0B28CB62', '2A00F387B399DCCB', '2A00E15A0A9CB200', '2A004620DB43DC89', '2A00A15D792EF3B0', '2A003DC80E810604', '2A0063ED92BCDB87', '2A007A02EEE67A50', '2A004979275AD782', '2A00131687C68656', '2A0014542F2F33A7', '2A00EB05A025AFDF', '2A0020B048380AF9', '2A00F0B5AD9E1D84', '2A00A9B718E596B4', '2A00C9534A9F1315', '2A00EA889708DB02', '2A00E9606C4F1D2B', '2A00E7F4F0F6CCB7', '2A0036B6BB44FA83', '2A004AC971FF35C0', '2A001B827E69E786', '2A008051B23343DD', '2A0059FB4BC15FE2', '2A00163AD1F86E2A', '2A0078C8318AB4EB', '2A006429BE028B5C', '2A00A5DFAAC9BE2F', '2A00F3671F552BC2', '2A00E68927148908', '2A004CF891C3BC76', '2A00601FA8D3E200', '2A0030EDE4ED

In [8]:
start_time = time.time()
for enu, i in enumerate(user_list):
    ranking_factorization_recomm = ranking_factorization_model.recommend(users=[i],k=10)
    ranking_factorization_recomm = ranking_factorization_recomm.remove_column('score')
    ranking_factorization_recomm.to_sql(conn, 'ml_recommendations')
    print(enu + 1, i)
end_time = time.time()
print(end_time - start_time)

1 2A005E25597F901F
2 2A00FC2A5756B0E3
3 2A002933A89E2195
4 2A00FC3EAB6D29E5
5 2A00ED27DFAA301C
6 2A000A3066472B32
7 2A00BB6460EE8382
8 2A0022BC39C185DA
9 2A00685913E603BE
10 2A0002D3077C1B1A
11 2A001BE9E78F1EE3
12 2A0080E161FBEC03
13 2A007AB60D581C88
14 2A00E11066A020B7
15 2A0051805EB6C0FC
16 2A00EF708C3BA02F
17 2A001670DBA6FBF9
18 2A0037FB0B28CB62
19 2A00F387B399DCCB
20 2A00E15A0A9CB200
21 2A004620DB43DC89
22 2A00A15D792EF3B0
23 2A003DC80E810604
24 2A0063ED92BCDB87
25 2A007A02EEE67A50
26 2A004979275AD782
27 2A00131687C68656
28 2A0014542F2F33A7
29 2A00EB05A025AFDF
30 2A0020B048380AF9
31 2A00F0B5AD9E1D84
32 2A00A9B718E596B4
33 2A00C9534A9F1315
34 2A00EA889708DB02
35 2A00E9606C4F1D2B
36 2A00E7F4F0F6CCB7
37 2A0036B6BB44FA83
38 2A004AC971FF35C0
39 2A001B827E69E786
40 2A008051B23343DD
41 2A0059FB4BC15FE2
42 2A00163AD1F86E2A
43 2A0078C8318AB4EB
44 2A006429BE028B5C
45 2A00A5DFAAC9BE2F
46 2A00F3671F552BC2
47 2A00E68927148908
48 2A004CF891C3BC76
49 2A00601FA8D3E200
50 2A0030EDE4ED3D19
51 2A0045

398 2A0016BA89770EA8
399 2A0042C113102E91
400 2A001580F901A241
401 2A00C995FF0D2E86
402 2A00D4581F0117AA
403 2A003DF01F737441
404 2A0066F4C5B1208F
405 2A008C2F263DA768
406 2A005DD97785E27B
407 2A002579EBE837FD
408 2A00A06337A9900F
409 2A00D271DC3121D6
410 2A003ECE569A5B43
411 2A00F17BDEB9FD00
412 2A005F2C9C55E926
413 2A00B7D7D53D2B64
414 2A006387FB057868
415 2A00E5CCF8E7FB00
416 2A00BD54A7658B58
417 2A00E1A8730903CF
418 2A002DA7676A5751
419 2A0073D687D466EB
420 2A00D1A70F7B81B3
421 2A004765E28F8F0A
422 2A00ADF53BBD5123
423 2A00190C36755E00
424 2A00CB2AE6964E2B
425 2A0036219AF927B0
426 2A00AAA82DA63D09
427 2A005D426E376E4F
428 2A00268F48409F00
429 2A00792CEE78E554
430 2A00523117397133
431 2A0009C1B52C4320
432 2A008C02465EFE0F
433 2A00890BFEA356CD
434 2A0085F6864D43A6
435 2A00BA9C03044BFB
436 2A00D89C9D7534F7
437 2A00A9449275C835
438 2A0050EED41101EF
439 2A002DE59BC63FD9
440 2A001D2ED6AA29C1
441 2A009D1F0394FB1B
442 2A00942580131C60
443 2A00582E70C205CE
444 2A0084136EA7FC37
445 2A009AB30

789 2A0022FC29ACB725
790 2A0086541D0EA65A
791 2A002B6066594027
792 2A00D5849BF5A700
793 2A007986A8E77E84
794 2A00269653EC61E6
795 2A00471EAE2DCB3D
796 2A0030147EB0E703
797 2A00C696B0AA022D
798 2A00EC51DB7B1580
799 2A00491B1A708884
800 2A00F48EC5EEA700
801 2A00EE535AA3D6B6
802 2A00CCC70F1351D5
803 2A0000B997182C54
804 2A008BB76C2D7311
805 2A00F0C3610F1562
806 2A004CBC49A00141
807 2A00C8DEE26467DE
808 2A00EB72A1881735
809 2A00D012D5E7E8FC
810 2A00A00CC36095F0
811 2A002FB67F6BD9CD
812 2A0046EA621AF00E
813 2A009D0F8C0E028C
814 2A00A00D170CC8C7
815 2A00EE7A4E4A5CFB
816 2A0006179DCF6ABC
817 2A0067888A38B45F
818 2A008C6D7C5AC4A6
819 2A00574C089AF323
820 2A00C913FBFC10F4
821 2A0029C60E5E37A8
822 2A00031241DF00A4
823 2A00B4403CD66593
824 2A0043D2C3E98D57
825 2A00D46B73475303
826 2A0006D2A0C4C56E
827 2A0062C442C197FF
828 2A001C5346A0996A
829 2A0068BB397574AA
830 2A000D544585412B
831 2A00F22E997A4759
832 2A009D280BB330D4
833 2A001F66DA810F98
834 2A00ED77EE774FD1
835 2A00EE9D87557995
836 2A0000A7B

1172 2A00F775869D6ABC
1173 2A00CA7A807ECBF0
1174 2A005D69CBFEB2B7
1175 2A00FB0DE2AE113F
1176 2A00675EBDA3FE4A
1177 2A00A1491E7E57C2
1178 2A004B297FB41C53
1179 2A006DB0BCAFD3D4
1180 2A008C9AB33EB3D5
1181 2A0090C000EA1155
1182 2A00CBE6F2259EBF
1183 2A00D1D297673168
1184 2A000AE5CEB3C3B4
1185 2A00B8954D782865
1186 2A002B3AE5BF73A3
1187 2A002133E0B1B19C
1188 2A006954838DA5DE
1189 2A00657F549208AE
1190 2A006FA80F4A84B1
1191 2A00CF1F561E5764
1192 2A00D080E5C6D0CB
1193 2A00072E485B3A73
1194 2A003421FF54261F
1195 2A00ACAC6A7218BB
1196 2A00FB754B6E0F0A
1197 2A002C27BA6B9486
1198 2A00253944C1FEAF
1199 2A00317C7D1B8251
1200 2A00E5EB5798A695
1201 2A005B2FD41ADFE1
1202 2A004D89E7DBA6C8
1203 2A0016A1FC4E2782
1204 2A002C7D382B8EBE
1205 2A00B32AA80644FD
1206 2A00E74E8C34355B
1207 2A005F9DC2C906B3
1208 2A007296275BDCF4
1209 2A0036D1C8C92D57
1210 2A0074DB3B1CFF14
1211 2A003C0A917B0087
1212 2A002D1B2EAF58D8
1213 2A006203C9CAA93A
1214 2A0095F9DA822140
1215 2A0061E9C7D93D17
1216 2A00A2E684E3007D
1217 2A008

1545 2A00CC0014C60EC3
1546 2A00CE9E52017CBF
1547 2A000CC8C44171FD
1548 2A0085CE163F723B
1549 2A0005584B18CCA9
1550 2A0041EFE41B606F
1551 2A00384905F26449
1552 2A002851A5A25531
1553 2A0067906B2B54DA
1554 2A00AD2B53A335F5
1555 2A00E45904EDB4C7
1556 2A008ED1FD28E3EA
1557 2A00A71276E199A3
1558 2A00FA3F6F6F88FF
1559 2A00700C8D5912D7
1560 2A00CCD6D455F3EE
1561 2A00D58A2A5AE026
1562 2A0099B9D96FDEF6
1563 2A000540A2B3203F
1564 2A00F98B1EBB9A69
1565 2A00DB311427599C
1566 2A00F680554BECCE
1567 2A00F68DFCE270C8
1568 2A006C70EE7D2C47
1569 2A0071048DE787E1
1570 2A00C7B3D6CB0F94
1571 2A00C2317CD70B20
1572 2A009A78E65DA5BF
1573 2A00F0ED711C03EE
1574 2A00E8EC6F94D402
1575 2A009E81FAE926A4
1576 2A000BA2255613BB
1577 2A0001D68388D0BC
1578 2A004C0467F997F8
1579 2A00CBD62B876F2F
1580 2A00DF676AC49D32
1581 2A003A83B0510407
1582 2A0049A819371C84
1583 2A00845CB2C97062
1584 2A00112936A6FE74
1585 2A001524431412AD
1586 2A0024091FB1ACB3
1587 2A002F32F3609FA0
1588 2A003E0A7A86719C
1589 2A00561A37EDF12D
1590 2A002

...

74853 2A0079E3091089CF
74854 2A00925272B3310A
74855 2A0052FDC9D1D232
74856 2A0075FB05B9099C
74857 2A00103B31C7882E
74858 2A0022AFAFD5B177
74859 2A007AC6F0C74557
74860 2A001FEF93D18A28
74861 2A00D244A0CE79A8
74862 2A002FFB1A55AAC4
74863 2A005B277FF48DB9
74864 2A001E2F764A0B9B
74865 2A0031A4CDB504E9
74866 2A00A421117826EC
74867 2A0055A7D0E98E33
74868 2A00F4868BF2D871
74869 2A0023099223753D
74870 2A00D81964F93439
74871 2A00E548EB33DFC3
74872 2A005559E98A1799
74873 2A007F89145ADC9D
74874 2A0022B5B48E0663
74875 2A00E5E241543879
74876 2A00523257E90518
74877 2A005ABF0CA887A8
74878 2A00426013C52536
74879 2A00364FDE4F30AA
74880 2A00851C982C686F
74881 2A003A64692BF393
74882 2A00CD623360F75E
74883 2A00624DA9388C0A
74884 2A006E2E9E13486B
74885 2A0083DD6EFE785D
74886 2A009246F297A61E
74887 2A00EA22CF4C7D76
74888 2A0048E2FBA4CAF5
74889 2A0070CAD7002A0B
74890 2A00C863651A0894
74891 2A00A5910228FF58
74892 2A009AA8BDE833AA
74893 2A000BF7C6DB9E10
74894 2A0041A6E85785A5
74895 2A0052759582E383
74896 2A00B

75210 2A002793CBF7DD4D
75211 2A0003E0924F583F
75212 2A00C266E492372E
75213 2A00D455631DA8FD
75214 2A00F389CA48DD8C
75215 2A00AEB0CF1DD554
75216 2A00DE88C428D06E
75217 2A002AC389575195
75218 2A0092EC748F7358
75219 2A0013A7245505DC
75220 2A00B0831AFA6F48
75221 2A002BDDF7FAB086
75222 2A00778CC45F08C6
75223 2A003D81A909E8A1
75224 2A003A9E7DC5C949
75225 2A00F98C52E16CB0
75226 2A00C1D3159DDB4A
75227 2A00FB499AF8C74E
75228 2A00DA702D025D40
75229 2A0051058AB5165F
75230 2A001C1FB5563ACE
75231 2A00D046AFE775E8
75232 2A00FB735FFC608A
75233 2A0091B0D2EC1F69
75234 2A00ED1B1CD541EC
75235 2A006187EE27F78D
75236 2A00CCF552B5B3E1
75237 2A00E08842B32DC7
75238 2A001D09A6B98BEA
75239 2A00F0026916DB39
75240 2A00F5633DEBD09C
75241 2A0025979130E7F9
75242 2A007FCBE8AB1058
75243 2A004806F5709CD2
75244 2A00620D43DAB436
75245 2A008038ACEA734D
75246 2A00B35AB6AE1FF7
75247 2A009B48DAA496BD
75248 2A00C39FE6AE2C24
75249 2A00E2CA821881C4
75250 2A00387A3F5304C9
75251 2A0080660486FA6B
75252 2A003A51ABDEBC19
75253 2A003

75568 2A004A17AE4EF7FC
75569 2A009FDBD4ED0147
75570 2A00682858F50363
75571 2A00E378EE281E3F
75572 2A008764943F92FA
75573 2A00B4CBDDA20602
75574 2A00427342A0A592
75575 2A00F801AF263733
75576 2A00CED4A9907B6D
75577 2A001A72B6271570
75578 2A00BE5F42FF5B3D
75579 2A0078500CE24296
75580 2A00F378666B0B50
75581 2A00C760C96F3592
75582 2A00BC672048B2E3
75583 2A00B22A10D4DA22
75584 2A000C5936AFEA7A
75585 2A005EE698E88317
75586 2A00D362E870C1C2
75587 2A005941A093D843
75588 2A003C96AEDE1299
75589 2A006D71146EC1EB
75590 2A00145AAAE671FD
75591 2A006E5439F16AF2
75592 2A0012E3332E0E62
75593 2A005B89AC4EC4CB
75594 2A006A8FD7DFB0B8
75595 2A0043C78509C9E7
75596 2A003ACDD7680917
75597 2A00E109F9C1F349
75598 2A00C722935CE9D4
75599 2A00D32A8B1D170F
75600 2A00EB51D5FED701
75601 2A00BB5AAD84511F
75602 2A001D05D2F10736
75603 2A008AA193EEE759
75604 2A00E08621174591
75605 2A00E8A2C2631713
75606 2A001146D8D412EE
75607 2A00A37817A557EF
75608 2A00DD9C5261BE45
75609 2A00A38487F81FEC
75610 2A00DA9BDC8CBDF6
75611 2A004

75926 2A00C4D97E5EB282
75927 2A0081FB5BEB453F
75928 2A009BDBB7495CCA
75929 2A004F1BA26DDC94
75930 2A00316B5F70F52F
75931 2A005D78FBCC2D97
75932 2A00EDBC63569A4D
75933 2A0055B32B998B94
75934 2A00BCB293D26F7F
75935 2A00C88CAEEA99E0
75936 2A002D6F0646F78D
75937 2A005308061716BF
75938 2A0063BC8573D89E
75939 2A00132708F40E6D
75940 2A008E9A8C6F73FA
75941 2A00CA3E4282FA11
75942 2A003BBA1D4C594E
75943 2A002E8FE7C824FF
75944 2A00F696B66E7DFE
75945 2A00977961D78B24
75946 2A00CAEE397D7F22
75947 2A007D0C5B889F33
75948 2A004F3F2E1FB549
75949 2A003F4C88AB878F
75950 2A0003A76913DD06
75951 2A007B139AB9BAC3
75952 2A00271967888DDF
75953 2A001940D7BAAE30
75954 2A0020966C44C49D
75955 2A00158F11FB94F5
75956 2A009D263F8630CD
75957 2A00AF8C7BC3FE48
75958 2A008D4D9CCC6380
75959 2A002D895BC6F235
75960 2A00C1599E9FC5F7
75961 2A006F3B14ABA9B7
75962 2A0045101D483769
75963 2A00CC84555EFB88
75964 2A0006CE8BEA1A58
75965 2A00E91E41889E97
75966 2A006C6FDCEC1E12
75967 2A00C1106554C116
75968 2A0002BBD6FFCDEC
75969 2A000

KeyboardInterrupt: 

In [9]:
start_time

1590131629.389091

In [20]:
popularity_model = turicreate.popularity_recommender.create(data, user_id='accountID', item_id='assetID', target='sum')
popularity_model

Preparing data set.

Data has 351665 observations with 79807 users and 5419 items.

Data prepared in: 0.620076s

351665 observations to process; with 5419 unique items.

Class                            : PopularityRecommender

Schema
------
User ID                          : accountID
Item ID                          : assetID
Target                           : sum
Additional observation features  : 0
User side features               : []
Item side features               : []

Statistics
----------
Number of observations           : 351665
Number of users                  : 79807
Number of items                  : 5419

Training summary
----------------
Training time                    : 0.0567

Model Parameters
----------------
Model class                      : PopularityRecommender

In [12]:
for i in user_list[:10]:
    popularity_recomm = popularity_model.recommend(users=[i],k=10)
    popularity_recomm = popularity_recomm.remove_column('score')
    print(popularity_recomm)

+------------------+----------+------+
|    accountID     | assetID  | rank |
+------------------+----------+------+
| 2A00E703A9C9D0CC | vod30937 |  1   |
| 2A00E703A9C9D0CC | vod11265 |  2   |
| 2A00E703A9C9D0CC | vod10097 |  3   |
| 2A00E703A9C9D0CC | vod11066 |  4   |
| 2A00E703A9C9D0CC | vod17553 |  5   |
| 2A00E703A9C9D0CC | vod11228 |  6   |
| 2A00E703A9C9D0CC | vod11103 |  7   |
| 2A00E703A9C9D0CC | vod8696  |  8   |
| 2A00E703A9C9D0CC | vod37081 |  9   |
| 2A00E703A9C9D0CC | vod29410 |  10  |
+------------------+----------+------+
[10 rows x 3 columns]

+------------------+----------+------+
|    accountID     | assetID  | rank |
+------------------+----------+------+
| 2A0065A3DC3CB444 | vod30937 |  1   |
| 2A0065A3DC3CB444 | vod11265 |  2   |
| 2A0065A3DC3CB444 | vod10097 |  3   |
| 2A0065A3DC3CB444 | vod11066 |  4   |
| 2A0065A3DC3CB444 | vod17553 |  5   |
| 2A0065A3DC3CB444 | vod11228 |  6   |
| 2A0065A3DC3CB444 | vod11103 |  7   |
| 2A0065A3DC3CB444 | vod8696  |  8   |
| 

In [42]:
popularity_recomm = popularity_model.recommend(users=['2A00000510F26CC4'],k=10)
popularity_recomm

Columns:
	accountID	str
	assetID	str
	score	float
	rank	int

Rows: 10

Data:
+------------------+----------+--------------------+------+
|    accountID     | assetID  |       score        | rank |
+------------------+----------+--------------------+------+
| 2A00000510F26CC4 | vod30937 |        82.5        |  1   |
| 2A00000510F26CC4 | vod11265 | 80.17647058823529  |  2   |
| 2A00000510F26CC4 | vod10097 | 75.05263157894737  |  3   |
| 2A00000510F26CC4 | vod11066 | 71.33582089552239  |  4   |
| 2A00000510F26CC4 | vod17553 | 55.55882352941177  |  5   |
| 2A00000510F26CC4 | vod11228 | 50.888888888888886 |  6   |
| 2A00000510F26CC4 | vod11103 | 46.17391304347826  |  7   |
| 2A00000510F26CC4 | vod8696  | 45.424050632911396 |  8   |
| 2A00000510F26CC4 | vod37081 | 44.400711020822754 |  9   |
| 2A00000510F26CC4 | vod29410 | 41.527472527472526 |  10  |
+------------------+----------+--------------------+------+
[10 rows x 4 columns]